In [0]:
from pyspark.sql import DataFrame
from pyspark.ml.feature import RegexTokenizer, HashingTF
from pyspark.ml.classification import LogisticRegression
from pyspark.ml import Pipeline
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

# load dataset
`docs` is training data

In [0]:
docs = sqlContext.read.parquet('/databricks-datasets/news20.binary/data-001/training').cache()

In [0]:
docs_test = sqlContext.read.parquet('/databricks-datasets/news20.binary/data-001/test')

In [0]:
docs_test.count()

Out[14]: 7532

# investigate training data

In [0]:
docs.count()

Out[4]: 11314

In [0]:
display(docs)

id text topic label 66954 From: mouse@thunder.mcrcim.mcgill.edu (der Mouse) Subject: Re: Creating 8 bit windows on 24 bit display.. How? Organization: McGill Research Centre for Intelligent Machines Lines: 59 In article <1993Apr16.093209.25719@fwi.uva.nl>, stolk@fwi.uva.nl (Bram) writes: > I am using an X server that provides 3 visuals: PseudoColor 8 bit, > Truecolor 24 bit and DirectColor 24 bit. Lucky dog... :-) > A problem occurs when I try to create a window with a visual that is > different from the visual of the parent (which uses the default > visual which is TC24). > In the Xlib reference guide from 'O reilly one can read in the > section about XCteateWindow, something like: > In the current implementation of X11: When using a visual other > than the parent's, be sure to create or find a suitable colourmap > which is to be used in the window attributes when creating, or > else a BadMatch occurs. > This warning, strangely enough, is only mentioned in the newer > editions of the X11R5 guides. It applies with equal force to earlier versions. Presumably only recently did the author(s) decide it was important enough to mention. The necessity it refers to has always been there, but it's been implicit in the way CreateWindow requests default some attributes of the new window. > However, even if I pass along a suitable colourmap, I still get a > BadMatch when I create a window with a non-default visual. > attr.colormap = cmap; > win = XCreateWindow( [...] > CopyFromParent, /* border width */ > 8, /* depth */ > InputOutput, /* class */ > vinfo.visual, /* visual */ > CWColormap, > &attr > ); This is because the warning you read is incomplete. You have to provide not only a colormap but also a border. The default border is CopyFromParent, which is not valid when the window's depth doesn't match its parent's. Specify a border-pixmap of the correct depth, or a border-pixel, and the problem should go away. There is another problem: I can't find anything to indicate that CopyFromParent makes any sense as the border_width parameter to XCreateWindow. Your Xlib implementation probably defines CopyFromParent as zero, to simplify the conversion to wire format, so you are unwittingly asking for a border width of zero, due to the Xlib implementation not providing stricter type-checking. (To be fair, I'm not entirely certain it's possible for Xlib to catch this.) der Mouse mouse@mcrcim.mcgill.edu comp.windows.x 0.0 58970 From: geb@cs.pitt.edu (Gordon Banks) Subject: Re: ORGAN DONATION AND TRANSPLANTATION FACT SHEET Reply-To: geb@cs.pitt.edu (Gordon Banks) Organization: Univ. of Pittsburgh Computer Science Lines: 26 In article <1993Apr13.150018.641@lmpsbbs.comm.mot.com> dougb@ecs.comm.mot.com writes: >My wife cannot donate blood because she has been to a malarial region >in the past three years. In fact, she tried to have her bone marrow >typed and they wouldn't even do that! Why? > The FDA, I believe. Rules say no blood or blood products donations from anyone who has been in a malarial area for 3 years. I was a platelet donor until my Thailand trip and my blood bank was very disappointed to find out they couldn't use me for 3 years. > >When the secretary of state asked me if I wanted to donate my >organs I said no because I figured that no one would want them >given my history. Was I correct? > Not necessarily. The same rules may not apply to organ donation as to blood donation. In fact, I'm sure they don't. -- ---------------------------------------------------------------------------- Gordon Banks N3JXP | "Skepticism is the chastity of the intellect, and geb@cadre.dsl.pitt.edu | it is shameful to surrender it too soon." ---------------------------------------------------------------------------- sci.med 1.0 76300 From: tclock@orion.oac.uci.edu (Tim Clock) Subject: Re: THE HAMAS WAY of DEATH Nntp-Posting-Host: orion.oac.uci.edu Organization: University of California, Irvine Lines: 15 In article <1993Apr17.160731.3178@nntpd.lkg.dec.com> alaa

In [0]:
display(docs.groupby('topic').count())

topic count comp.windows.x 593 misc.forsale 585 rec.sport.hockey 600 rec.sport.baseball 597 talk.politics.guns 546 talk.politics.misc 465 comp.os.ms-windows.misc 591 comp.sys.ibm.pc.hardware 590 comp.graphics 584 soc.religion.christian 599 comp.sys.mac.hardware 578 talk.religion.misc 377 talk.politics.mideast 564 rec.motorcycles 598 rec.autos 594 alt.atheism 480 sci.electronics 591 sci.space 593 sci.med 594 sci.crypt 595

In [0]:
display(docs.filter(docs.topic.like('sci.%')))

id text topic label 58970 From: geb@cs.pitt.edu (Gordon Banks) Subject: Re: ORGAN DONATION AND TRANSPLANTATION FACT SHEET Reply-To: geb@cs.pitt.edu (Gordon Banks) Organization: Univ. of Pittsburgh Computer Science Lines: 26 In article <1993Apr13.150018.641@lmpsbbs.comm.mot.com> dougb@ecs.comm.mot.com writes: >My wife cannot donate blood because she has been to a malarial region >in the past three years. In fact, she tried to have her bone marrow >typed and they wouldn't even do that! Why? > The FDA, I believe. Rules say no blood or blood products donations from anyone who has been in a malarial area for 3 years. I was a platelet donor until my Thailand trip and my blood bank was very disappointed to find out they couldn't use me for 3 years. > >When the secretary of state asked me if I wanted to donate my >organs I said no because I figured that no one would want them >given my history. Was I correct? > Not necessarily. The same rules may not apply to organ donation as to blood donation. In fact, I'm sure they don't. -- ---------------------------------------------------------------------------- Gordon Banks N3JXP | "Skepticism is the chastity of the intellect, and geb@cadre.dsl.pitt.edu | it is shameful to surrender it too soon." ---------------------------------------------------------------------------- sci.med 1.0 58953 From: robin@ntmtv.com (Robin Coutellier) Subject: Critique of Pressure Point Massager Originator: robin@volans Nntp-Posting-Host: volans Reply-To: robin@ntmtv.com (Robin Coutellier) Organization: Northern Telecom Inc, Mountain View, CA Distribution: na Lines: 141 As promised, below is a personal critique of a Pressure Point Massager I recently bought from the Self Care Catalog. I am very pleased with the results. The catalog description is as follows: The Pressure Point Massager is an aggressive physical massager that actually kneads the tension out of muscles ... much like a professional shiatsu masseur. The powerful motor drives two counter-rotating "thumbs" that move in one-inch orbits -- releasing tension in the neck, back, legs and arms. Pressure Point Massager A2623 $109 To order or receive a catalog, call (24 hours, 7 days) 1-800-345-3371 or fax at 1-800-345-4021. ******** NOTE: When I ordered the massager, the item number was different, and the price was $179, not $109. When I received it, I glanced thru the newer catalog enclosed with it to see anything was different from the first one. I was QUITE annoyed to see a $70 difference in price. I called them about it, and the cust rep said that they had switched manufacturers, although it looks and works exactly the same. He told me to go ahead and return the first one and order the cheaper one, using the price difference as a reason for return. In fact, since the newer ones might take a while to ship from the factory (I received this one in 3 days), he told me I could use the one I already have until the new one arrives, then return the old one. VERY reasonable people. ******** I have long-term neck, shoulder and back pain (if I were a building, I would be described as "structurally unsound :-) ). I have stretches and exercises to do that help, but the problem never really goes away. If, for whatever reason, I do not exercise for a while (illness, not enough time, lazy, etc.), the muscles become quite stiff and painful and, thus, more prone to further strain. Even with exercise, I sometimes require physical therapy to get back on track, which 1st requires a doctor visit to get the prescription for p.t. The tension in my neck, if not released, eventually causes a headache (sometimes confused with a sinus headache) over my left eye. When my physical therapist has massaged my neck, and the sub-occipital muscles in particular (the 2 knobby areas near the base of the skull), the headache usually eased within a day, although it hurts like hell to while it is being massaged. I ordered this device because it seemed to be exactly what I was wishing someone woul

In [0]:
display(docs.groupby('label').count())

label count 0.0 8941 1.0 2373

# create labels
1 = science, 0 = non-science

In [0]:
def preprocess(dataFrame):
  return dataFrame.withColumn('label',
                             dataFrame.topic.like('sci.%').cast('double')) \
                  .cache()

In [0]:
training = preprocess(docs)
display(training.groupBy('label').count())

label count 0.0 8941 1.0 2373

In [0]:
test = preprocess(docs_test)
display(test.groupBy('label').count())

label count 0.0 5953 1.0 1579

# ML Pipelines: Classifying newsgroup articles
### set-up ML pipeline with three stages:
##### 1. tokenizer
##### 2. hashingTF
##### 3. LogisticRegression

In [0]:
# next line has the bug
#tokenizer = RegexTokenizer(inputCol='text', outputCol='words', pattern='s')

# next line is fixed
tokenizer = RegexTokenizer(inputCol='text', outputCol='words', pattern='\\s+')

hashingTF = HashingTF(inputCol=tokenizer.getOutputCol(), outputCol='features', numFeatures=5000)

lr = LogisticRegression(maxIter=20, regParam=0.01)

pipeline = Pipeline(stages=[tokenizer, hashingTF, lr])

### train model

In [0]:
model = pipeline.fit(training)

### evaluate prediction results: training

In [0]:
predictions = model.transform(training)
display(predictions.select('topic', 'label', 'prediction', 'text'))

topic label prediction text comp.windows.x 0.0 0.0 From: mouse@thunder.mcrcim.mcgill.edu (der Mouse) Subject: Re: Creating 8 bit windows on 24 bit display.. How? Organization: McGill Research Centre for Intelligent Machines Lines: 59 In article <1993Apr16.093209.25719@fwi.uva.nl>, stolk@fwi.uva.nl (Bram) writes: > I am using an X server that provides 3 visuals: PseudoColor 8 bit, > Truecolor 24 bit and DirectColor 24 bit. Lucky dog... :-) > A problem occurs when I try to create a window with a visual that is > different from the visual of the parent (which uses the default > visual which is TC24). > In the Xlib reference guide from 'O reilly one can read in the > section about XCteateWindow, something like: > In the current implementation of X11: When using a visual other > than the parent's, be sure to create or find a suitable colourmap > which is to be used in the window attributes when creating, or > else a BadMatch occurs. > This warning, strangely enough, is only mentioned in the newer > editions of the X11R5 guides. It applies with equal force to earlier versions. Presumably only recently did the author(s) decide it was important enough to mention. The necessity it refers to has always been there, but it's been implicit in the way CreateWindow requests default some attributes of the new window. > However, even if I pass along a suitable colourmap, I still get a > BadMatch when I create a window with a non-default visual. > attr.colormap = cmap; > win = XCreateWindow( [...] > CopyFromParent, /* border width */ > 8, /* depth */ > InputOutput, /* class */ > vinfo.visual, /* visual */ > CWColormap, > &attr > ); This is because the warning you read is incomplete. You have to provide not only a colormap but also a border. The default border is CopyFromParent, which is not valid when the window's depth doesn't match its parent's. Specify a border-pixmap of the correct depth, or a border-pixel, and the problem should go away. There is another problem: I can't find anything to indicate that CopyFromParent makes any sense as the border_width parameter to XCreateWindow. Your Xlib implementation probably defines CopyFromParent as zero, to simplify the conversion to wire format, so you are unwittingly asking for a border width of zero, due to the Xlib implementation not providing stricter type-checking. (To be fair, I'm not entirely certain it's possible for Xlib to catch this.) der Mouse mouse@mcrcim.mcgill.edu sci.med 1.0 1.0 From: geb@cs.pitt.edu (Gordon Banks) Subject: Re: ORGAN DONATION AND TRANSPLANTATION FACT SHEET Reply-To: geb@cs.pitt.edu (Gordon Banks) Organization: Univ. of Pittsburgh Computer Science Lines: 26 In article <1993Apr13.150018.641@lmpsbbs.comm.mot.com> dougb@ecs.comm.mot.com writes: >My wife cannot donate blood because she has been to a malarial region >in the past three years. In fact, she tried to have her bone marrow >typed and they wouldn't even do that! Why? > The FDA, I believe. Rules say no blood or blood products donations from anyone who has been in a malarial area for 3 years. I was a platelet donor until my Thailand trip and my blood bank was very disappointed to find out they couldn't use me for 3 years. > >When the secretary of state asked me if I wanted to donate my >organs I said no because I figured that no one would want them >given my history. Was I correct? > Not necessarily. The same rules may not apply to organ donation as to blood donation. In fact, I'm sure they don't. -- ---------------------------------------------------------------------------- Gordon Banks N3JXP | "Skepticism is the chastity of the intellect, and geb@cadre.dsl.pitt.edu | it is shameful to surrender it too soon." ---------------------------------------------------------------------------- talk.politics.mideast 0.0 0.0 From: tclock@orion.oac.uci.edu (Tim Clock) Subject: Re: THE HAMAS WAY of DEATH Nntp-Posting-Host: orion.oac.uci.edu Organization: University of California, Irvine Lines: 15 In article <1993Apr17.160731.

In [0]:
evaluator = BinaryClassificationEvaluator(metricName='areaUnderROC')
evaluator.evaluate(predictions)

Out[33]: 0.9996588112179702

### evaluate prediction results: test

In [0]:
evaluator.evaluate(model.transform(test))

Out[34]: 0.899033244051171

# WHAT??!
##### let's debug

### examine intermediate results
observations:   
`words` column should be individual words from text; pre-processing is not chunking it correctly   
`tokenizer` used `pattern='s'`; we want by white space

In [0]:
predictions.printSchema()

root
-- id: string (nullable = true)
-- text: string (nullable = true)
-- topic: string (nullable = true)
-- label: double (nullable = true)
-- words: array (nullable = true)
 |-- element: string (containsNull = true)
-- features: vector (nullable = true)
-- rawPrediction: vector (nullable = true)
-- probability: vector (nullable = true)
-- prediction: double (nullable = false)

In [0]:
display(predictions.select('label', 'words'))

label words 0.0 List(from: mou, e@thunder.mcrcim.mcgill.edu (der mou, e) , ubject: re: creating 8 bit window, on 24 bit di, play.. how? organization: mcgill re, earch centre for intelligent machine, line, : 59 in article <1993apr16.093209.25719@fwi.uva.nl>, , tolk@fwi.uva.nl (bram) write, : > i am u, ing an x , erver that provide, 3 vi, ual, : p, eudocolor 8 bit, > truecolor 24 bit and directcolor 24 bit. lucky dog... :-) > a problem occur, when i try to create a window with a vi, ual that i, > different from the vi, ual of the parent (which u, e, the default > vi, ual which i, tc24). > in the xlib reference guide from 'o reilly one can read in the > , ection about xcteatewindow, , omething like: > in the current implementation of x11: when u, ing a vi, ual other > than the parent', , be , ure to create or find a , uitable colourmap > which i, to be u, ed in the window attribute, when creating, or > el, e a badmatch occur, . > thi, warning, , trangely enough, i, only mentioned in the newer > edition, of the x11r5 guide, . it applie, with equal force to earlier ver, ion, . pre, umably only recently did the author(, ) decide it wa, important enough to mention. the nece, ity it refer, to ha, alway, been there, but it', been implicit in the way createwindow reque, t, default , ome attribute, of the new window. > however, even if i pa, along a , uitable colourmap, i , till get a > badmatch when i create a window with a non-default vi, ual. > attr.colormap = cmap; > win = xcreatewindow( [...] > copyfromparent, /* border width */ > 8, /* depth */ > inputoutput, /* cla, */ > vinfo.vi, ual, /* vi, ual */ > cwcolormap, > &attr > ); thi, i, becau, e the warning you read i, incomplete. you have to provide not only a colormap but al, o a border. the default border i, copyfromparent, which i, not valid when the window', depth doe, n't match it, parent', . , pecify a border-pixmap of the correct depth, or a border-pixel, and the problem , hould go away. there i, another problem: i can't find anything to indicate that copyfromparent make, any , en, e a, the border_width parameter to xcreatewindow. your xlib implementation probably define, copyfromparent a, zero, to , implify the conver, ion to wire format, , o you are unwittingly a, king for a border width of zero, due to the xlib implementation not providing , tricter type-checking. (to be fair, i'm not entirely certain it', po, ible for xlib to catch thi, .) der mou, e mou, e@mcrcim.mcgill.edu ) 1.0 List(from: geb@c, .pitt.edu (gordon bank, ) , ubject: re: organ donation and tran, plantation fact , heet reply-to: geb@c, .pitt.edu (gordon bank, ) organization: univ. of pitt, burgh computer , cience line, : 26 in article <1993apr13.150018.641@lmp, bb, .comm.mot.com> dougb@ec, .comm.mot.com write, : >my wife cannot donate blood becau, e , he ha, been to a malarial region >in the pa, t three year, . in fact, , he tried to have her bone marrow >typed and they wouldn't even do that! why? > the fda, i believe. rule, , ay no blood or blood product, donation, from anyone who ha, been in a malarial area for 3 year, . i wa, a platelet donor until my thailand trip and my blood bank wa, very di, appointed to find out they couldn't u, e me for 3 year, . > >when the , ecretary of , tate a, ked me if i wanted to donate my >organ, i , aid no becau, e i figured that no one would want them >given my hi, tory. wa, i correct? > not nece, arily. the , ame rule, may not apply to organ donation a, to blood donation. in fact, i'm , ure they don't. -- ---------------------------------------------------------------------------- gordon bank, n3jxp | ", keptici, m i, the cha, tity of the intellect, and geb@cadre.d, l.pitt.edu | it i, , hameful to , urrender it too , oon." ---------------------------------------------------------------------------- ) 0.0 List(from: tclock@orion.oac.uci.edu (tim clock) , ubject: re: the hama, way of death nntp-po, ting-ho, t: orion.oac.uci.edu organization: univer, ity of california, irv

# Tune hyper-parameters via k-fold cross validation
### search over grid: # features by regularization
### optimize based on metric: area under ROC curve

In [0]:
paramGrid = ParamGridBuilder() \
            .addGrid(hashingTF.numFeatures, [1000, 10000]) \
            .addGrid(lr.regParam, [0.05, 0.2]) \
            .build()

In [0]:
cv = CrossValidator(estimator=pipeline,
                    evaluator=evaluator,
                    estimatorParamMaps=paramGrid,
                    numFolds=2)

cvModel = cv.fit(training)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [0]:
evaluator.evaluate(cvModel.transform(test))

Out[38]: 0.9253106479965998

# save predictions

In [0]:
#output_file_name = 'prediction_results'
#cvModel.transform(test).select('id', 'prediction') \
#       .write.json(output_file_name)